<a href="https://colab.research.google.com/github/fbeilstein/machine_learning/blob/master/workbook_02_python.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Run the following block to get helper functions `%%debug_cell_with_pytutor` and `%%embed_into_game`. Explanation follows.

In [0]:
#@title #Black magic (just run it to get few helper functions)

!curl -O https://raw.githubusercontent.com/fbeilstein/machine_learning/master/pytutor/data_begin.html
!curl -O https://raw.githubusercontent.com/fbeilstein/machine_learning/master/pytutor/data_end.html
!curl -O https://raw.githubusercontent.com/fbeilstein/machine_learning/master/pytutor/pg_encoder.py
!curl -O https://raw.githubusercontent.com/fbeilstein/machine_learning/master/pytutor/pg_logger.py
!sudo apt-get install graphviz libgraphviz-dev python-dev
!pip install pylint pygraphviz

from IPython.core.magic import  Magics, magics_class, cell_magic, line_magic

@magics_class
class Helper(Magics):

  def __init__(self, shell=None,  **kwargs):
    super().__init__(shell=shell, **kwargs)
    with open('data_begin.html', 'r') as f_in:
      lines = f_in.readlines()
      self.begin_debug = "".join(lines)
    with open('data_end.html', 'r') as f_in:
      lines = f_in.readlines()
      self.end_debug = "".join(lines)

  @cell_magic
  def debug_cell_with_pytutor(self, line, cell):
    import json
    import bdb
    from pg_logger import PGLogger
    import IPython
    from google.colab import output
    
    def cgi_finalizer(input_code, output_trace):
      ret = dict(code=input_code, trace=output_trace)
      json_output = json.dumps(ret, indent=None) # use indent=None for most compact repr
      display(IPython.display.HTML("<html>" + self.begin_debug + json_output + self.end_debug + "</html>"))

    primitives = line == 'primitives'
    logger = PGLogger(cumulative_mode=False,
                  heap_primitives=primitives, 
                  show_only_outputs=False, 
                  finalizer_func=cgi_finalizer,
                  disable_security_checks=True,
                  allow_all_modules=True,
                  probe_exprs=False)

    try:
      logger._runscript(cell)
    except bdb.BdbQuit:
      print("INTERNAL ERROR OCCURED")
    finally:
      logger.finalize()

  @cell_magic
  def plot_uml(self, line, cell):
    f = open("temp.py", "w+")
    f.write(cell)
    f.close()
    import os
    os.system('pyreverse -A -o png -p img temp.py')
    from IPython.display import Image
    from google.colab import output
    display(Image('classes_img.png'))

  @cell_magic
  def uml_and_debug(self, line, cell):
    self.plot_uml(line, cell)
    self.debug_cell_with_pytutor(line, cell)

  @cell_magic
  def embed_into_game(self, line, cell):
    games = {'snake': self._snake_game,
             'ball': self._bouncing_ball,
             'walker': self._walker}
    games[line](cell)

  def _snake_game(self, python_code):
    str_begin = '''
<script type="text/javascript" src="https://brython.info/src/brython.js"></script>
<script type="text/javascript" src="https://brython.info/src/brython_stdlib.js"></script>
<script type="text/python3">
    '''
    str_end = '''
from browser import document, svg, timer

class Field:
  def __init__(self, w, h):
    self.rects = [[svg.rect(x=40*i, y=40*j, width=38, height=38, fill='#000000') for i in range(w)] for j in range(h)]
    self.panel = document['panel']
    for row in self.rects:
      for rect in row:
        self.panel <= rect

  def clear(self):
    for row in self.rects:
      for rect in row:
        rect.attrs['fill'] = '#000000'

  def draw_snake(self, snake):
    for i,j in snake:
      (self.rects[j][i]).attrs['fill'] = '#00AA00'

  def draw_apple(self, apple):
    i,j = apple
    (self.rects[j][i]).attrs['fill'] = '#AA0000'

field = Field(15, 15)
snake = Snake(15, 15)
snake.reset()
apple = Apple(15, 15)
apple.reset()

def keyCode(ev):
  ev.stopPropagation()
  snake.set_direction({87:[0,-1], 83:[0,1], 65:[-1,0], 68:[1,0]}[int(ev.keyCode)])

document.onkeydown = keyCode

def evolute():
  snake.move_one_step()
  if snake.head_collision():
    snake.reset()
    apple.reset()
  field.clear()
  field.draw_apple(apple.get_apple())
  field.draw_snake(snake.get_snake())
  head = snake.get_snake()[0]
  a = apple.get_apple()
  if head[0] == a[0] and head[1] == a[1]:
    snake.grow_on_next_step()
    apple.reset()
    
loop = timer.set_interval(evolute, 300)

</script>

<div id="errors" style="position:absolute; max-width:400px;"></div>

<svg xmlns="http://www.w3.org/2000/svg" xmlns:xlink="http://www.w3.org/1999/xlink" 
    width="600" height="600" style="border-style:solid;border-width:1;border-color:#000;">
  <g id="panel">
  </g>
</svg>

<script>
console.log = text =>
{
    var highestTimeoutId = setTimeout(";");
    for (var i = 0 ; i < highestTimeoutId ; i++) {
        clearTimeout(i); 
    }
    let element = document.getElementById("errors");
    element.innerHTML += text.replace('\\n', '<br>') + '<br>';
}
brython(1)
</script>    '''
    import IPython
    from google.colab import output
    display(IPython.display.HTML(str_begin + python_code + str_end))

  def _bouncing_ball(self, python_code):
    str_begin = '''
    <script src="https://pyodide.cdn.iodide.io/pyodide.js"></script>

<script>
   window.languagePluginUrl = "/pyodide.js";
   languagePluginLoader.then(() => {
     pyodide.runPython(`
from js import document

class Ball:
  def move_and_view(): pass
class Block:
  def move_and_view(): pass
def publish_message(): pass
    '''
    str_end = '''
canvas = document.getElementById("canvas")
canvas.setAttribute('width', total_w)
canvas.setAttribute('height', total_h)
ctx = canvas.getContext("2d")
show_must_go_on = True

## hacking the ball class
old_f1 = Ball.move_and_view
def draw_ball(ball, *args, **kwargs):
  old_f1(ball, *args, **kwargs)
  p = ball.get_coordinates()
  x, y = p.x, p.y
  r_ball, color = ball.get_properties()
  ctx.beginPath()
  ctx.arc(x, total_h-y, r_ball, 0.0, 2.0 * 3.1415, 0)
  ctx.fillStyle = color
  ctx.fill()
  ctx.lineWidth = 3;
  ctx.strokeStyle = 'black'
  ctx.stroke()
Ball.move_and_view = draw_ball

## hacking the block class
old_f2 = Block.move_and_view
def draw_block(block, *args, **kwargs):
  old_f2(block, *args, **kwargs)
  P, S = block.get_sizes()
  color = block.get_properties()
  ctx.fillStyle = color
  ctx.fillRect(P.x, total_h-P.y-S.y, S.x, S.y)
  ctx.strokeStyle = 'black'
  ctx.strokeRect(P.x, total_h-P.y-S.y, S.x, S.y)
Block.move_and_view = draw_block

## hacking message
def draw_message(msg):
  ctx.font = "30px Arial"
  ctx.textAlign = "center"
  ctx.fillStyle = "black"
  ctx.fillText(msg, total_w/2, total_h/2)
publish_message = draw_message

## hacking keywait
class ImmediateStop(Exception): pass
old_wfk = wait_for_key_and_start
def wait_for_key_and_start():
  global show_must_go_on
  show_must_go_on = False
  raise ImmediateStop

key_status = {188: False, 190: False, 90: False, 88: False}
send_back_key = [0, 0]

def onkeydown(event):
  code = int(event.which)
  key_code = code #chr(code)
  global show_must_go_on
  if not show_must_go_on:
    if key_code == 13:
      old_wfk()
      show_must_go_on = True
    return

  directions_up   = {188: -1, 190: 1}
  directions_down = { 90: -1,  88: 1}

  if key_code in directions_up:
    send_back_key[0] = directions_up[key_code]
  if key_code in directions_down:
    send_back_key[1] = directions_down[key_code]
  if key_code in key_status.keys():
    key_status[key_code] = True

def onkeyup(event):
  code = int(event.which)
  key_code = code #chr(code)
  directions_up   = [188, 190]
  directions_down = [90,  88]
  if key_code in key_status.keys():
    key_status[key_code] = False
  if not key_status[directions_up[0]] and not key_status[directions_up[1]]:
    send_back_key[0] = 0
  if not key_status[directions_down[0]] and not key_status[directions_down[1]]:
    send_back_key[1] = 0

canvas.setAttribute('tabindex', '0')
canvas.addEventListener('keyup', onkeyup)
canvas.addEventListener('keydown', onkeydown)

def evolute():
    #print('YO')
    if not show_must_go_on:
        return
    ctx.clearRect(0, 0, canvas.width, canvas.height) # cleanup before start
    ctx.strokeRect(0, 0, canvas.width, canvas.height) # field
    try:
        timer_tick(send_back_key[1], send_back_key[0])
    except ImmediateStop:
        pass



##############################


    `)
  })


function timer_tick() {
    pyodide.runPython(`evolute()`);
}

languagePluginLoader.then(() => {
  setInterval(timer_tick, 10);
  })

</script>

<div id="errors" style="position:absolute; max-width:800px;"></div>
<canvas id="canvas" width="1000" height="600"></canvas>

<script>
console.log = text =>
{
    var highestTimeoutId = setTimeout(";");
    for (var i = 0 ; i < highestTimeoutId ; i++) {
        clearTimeout(i);
    }
    let element = document.getElementById("errors");
    element.innerHTML += text.replace('\\n', '<br>') + '<br>';
}
</script>
'''
    import IPython
    from google.colab import output
    display(IPython.display.HTML(str_begin + python_code + str_end))

  def _walker(self, python_code):
    str_begin = '''
<script type="text/javascript" src="https://brython.info/src/brython.js"></script>
<script type="text/javascript" src="https://brython.info/src/brython_stdlib.js"></script>
<script type="text/python3">
    '''
    str_end = '''
from browser import document, svg, timer

class Field:
  def __init__(self, w, h):
    self.rects = [[svg.rect(x=40*i, y=40*j, width=38, height=38, fill='#000000') for i in range(w)] for j in range(h)]
    self.panel = document['panel']
    for row in self.rects:
      for rect in row:
        self.panel <= rect

  def clear(self):
    for row in self.rects:
      for rect in row:
        rect.attrs['fill'] = '#000000'

  def draw_walker(self, apple):
    i,j = apple
    (self.rects[j][i]).attrs['fill'] = '#AA0000'

field = Field(15, 15)
walker = Walker(8, 8, 15, 15)

def keyCode(ev):
  ev.stopPropagation()
  walker.step(*({87:[0,-1], 83:[0,1], 65:[-1,0], 68:[1,0]}[int(ev.keyCode)]))

document.onkeydown = keyCode

def evolute():
  field.clear()
  field.draw_walker(walker.get_position())
    
loop = timer.set_interval(evolute, 300)

</script>

<div id="errors" style="position:absolute; max-width:400px;"></div>

<svg xmlns="http://www.w3.org/2000/svg" xmlns:xlink="http://www.w3.org/1999/xlink" 
    width="600" height="600" style="border-style:solid;border-width:1;border-color:#000;">
  <g id="panel">
  </g>
</svg>

<script>
console.log = text =>
{
    var highestTimeoutId = setTimeout(";");
    for (var i = 0 ; i < highestTimeoutId ; i++) {
        clearTimeout(i); 
    }
    let element = document.getElementById("errors");
    element.innerHTML += text.replace('\\n', '<br>') + '<br>';
}
brython(1)
</script>
    '''
    import IPython
    from google.colab import output
    display(IPython.display.HTML(str_begin + python_code + str_end))



## use ipython load_ext mechanism here if distributed
get_ipython().register_magics(Helper)
from IPython.display import clear_output
clear_output()

# Learn to debug

The following code generates list of lists that contain strings of a form 'row,column'.

* **problem 1:** run the script and see its output
* **problem 2:** add at the top of the cell `%%debug_cell_with_pytutor` to run a debugger. Use debugger to undestand how the code works.

In [0]:
%%debug_cell_with_pytutor
import numpy as np

X = np.array([[1,2],[3,4],[5,6]])

total_list = []
for i in range(3):
  l = []
  for j in range(3):
    l.append('{},{}'.format(i,j))
  total_list.append(l)
total_list

#Basic Python

##Simple iterations and conditions

* **Problem 1:** write the code that prints all numbers in range $0$-$100$ divisible by $3$.

* **Problem 2:** modify your code so that if number is also divisible by $5$ it is omitted.

**Note 1:** you can use debugger intensively (add ``%%debug_cell_with_pytutor`` at the top of the cell).

**Note 2:** if you fill stuck, google for `for` loops in Python and search any example with `range`.

In [0]:
# Enter your code here

##Indexing, slicing, iteration

* **Problem 1:** Create a list containing items ```"machine"```, ```"learning"```, ```"is"```, ```"awesome"```
* **Problem 2:** Print the entire list with simple print
* **Problem 3:** Print the entire list with ```for``` cycle
* **Problem 4:** Use slicing to get a new list that contains ```"machine"```, ```"learning"```, print it
* **Problem 5:** Use indexing to get the word ```"awesome"``` from the list (as a string, not list!)
* **Problem 6:** Using slice assignment, change ```"machine"```, ```"learning"``` to ```"theoretical"```, ```"physics"```
* **Problem 7:** Use ```append``` to add ```"sometimes"``` at the end of the list
* **Problem 8:** Create list containing numbers $1$ to $5$ and list containing characters 'a', 'b', and 'c'. Experiment with slice assignments, try different sizes of the assigned list slice and the assignee list slice. Try assigning slices of the current list to its own other slices. What happens when their ranges overlap?

**Note:** you can use debugger intensively (add ``%%debug_cell_with_pytutor`` at the top of the cell).

In [0]:
# Enter your code here

##2-dimensional array

* **Problem:** consider the following code in debug mode; understand how two-dimensional lists work.

In [0]:
%%debug_cell_with_pytutor

matrix = [[1, 2, 3],
          [4, 5, 6],
          [7, 8, 9]]
print(matrix)
print(matrix[1])
print(matrix[1][1])
print(matrix[2][0])

##Changing list during iteration

In [0]:
%%debug_cell_with_pytutor primitives

L = [1, 2, 3, 4, 5]

for x in L:
  x = 17

print(L)

for i in range(len(L)):
  L[i] = 17

print(L)

##Deep and shallow copy

In [0]:
%%debug_cell_with_pytutor

L = [1, 2, 3]
M = [4, L, 5]

X = M
Y = M.copy()
import copy
Z = copy.deepcopy(M)

print("nocopy: ", X, "; copy: ", Y, "; deepcopy", Z)
M[0] = 11
print("nocopy: ", X, "; copy: ", Y, "; deepcopy", Z)
L[1] = 25
print("nocopy: ", X, "; copy: ", Y, "; deepcopy", Z)

##Comprehensions

**Provblem:** 
* Explore the following code with debugger
* Understand syntaxis of comprehension

In [0]:
%%debug_cell_with_pytutor

L = [i**2 for i in range(5)] # list comprehension
D = {k: v for k,v in zip(range(5), L)} # dictionary comprehension
print(L, D)

L = list(zip(range(5), range(5)))
D = dict(zip(range(5), range(5)))
print(L, D)

D = {k: k**2 for k in range(5)} # dictionary comprehension
print(D)

##Use list comprehension

**Problem:** Create a list of all numbers from $1$ to $100$ that satisfy $n^2 \text{ mod } 7 = 3$. Use
* Cycle and nested if
* List comprehension (full form with for and if)

**Note:** you may want to check this [Python Software Fundation Article](https://docs.python.org/3/tutorial/datastructures.html#list-comprehensions) if you have never seen list comprehension syntax.

In [0]:
# Enter your code here

##More complex iteration techniques

Consider the following snippets.
Make sure you understand syntaxis and how iteration is performed.
Use debugger if needed.

In [0]:
#iterating two lists simultaneously

L1 = [1, 2, 3, 4, 5]
L2 = [5, 4, 3, 2, 1]

for x,y in zip(L1, L2):
  print(x, " -- ", y)

In [0]:
#Iterating list and indices simultaneously

L = [1, 2, 3, 4, 5]

for i, v in enumerate(L):
  print(i, "-th element is ", v)

##Dictionary

* **Problem 1:** create Python dictionary that contains the following data

Language | Creator
---|---
Perl | Larry Wall 
Tcl | John Ousterhout 
Python | Guido van Rossum

* **Problem 2:** get creator of Python from the dictionary
* **Problem 3:** print language and its creator separated by colon (:), each programming language should be printed on a separate line
* **Problem 4:** explore different options for iteration through dictionary, e.g. iterate through: `table.keys()`, `table`, `table.values()`, and `table.items()`. 

**Note:** you can use debugger intensively (add ``%%debug_cell_with_pytutor`` at the top of the cell).

In [0]:
# Enter your code here

##Shared references

* **Problem 1:** consider the following code in debug mode; understand how references work.
* **Problem 2:** modify the code so that lists are copied, observe the result.

**Note:** you can use debugger intensively (add ``%%debug_cell_with_pytutor`` at the top of the cell).

**Example 1:**

In [0]:
%%debug_cell_with_pytutor

X = [1, 2, 3]
L = ['a', X, 'b']
D = {'x':X, 'y':2}

print(L)
print(D)

X[1] = 'surprise' # changes all 3 references!
print(L)
print(D)

**Example 2:**

In [0]:
%%debug_cell_with_pytutor

L = [1, 2, 3]
M = ['X', L, 'Y']
print(L)
print(M)

L[1] = 0
print(L)
print(M)

**Example 3:**

In [0]:
%%debug_cell_with_pytutor
def changer(a, b):
  a = 2             # changes local name's value only
  b[0] = 'spam'     # changes shared object in-place

X = 1
L = [1, 2]
changer(X, L)
X, L

##Repetition adds one level

**Problem:** 
* create a list ```X``` containing numbers 1,2,3,4
* create a list ```Y``` as 3 repetitions of ```X```, i.e. ```X * 3```
* create a list ```Z``` as 3 repetitions of ```[X]```, i.e. ```[X] * 3```
* print these lists
* change list ```X``` somehow
* print all lists again
* observe the result and do conclusions; use debugger to understand better how everything works


In [0]:
# Enter your code here

##Simple while

**Problem:** let's consider [The Collatz conjecture](https://en.wikipedia.org/wiki/Collatz_conjecture). Suppose it is true (probably it really is, but for now we  don't have any rigorous proof) and write the code that generates an appropriate sequence. The rules are as follows:

* $a_{n+1} = \cfrac{a_n}{2}$ if $a_n$ is even;
* $a_{n+1} = 3 a_n + 1$ if $a_n$ is odd;
* procedure terminates when $a_n$ is equal to $1$.

Think about using the ```while``` cycle

In [0]:
# Enter your code here

##Continue

**Problem:** 

* Consider the following code. Its purpose is to find all such pairs of ```x``` and ```y``` (taken from lists ```X``` and ```Y``` respectively) such that ```x % 17 == m1``` and ```y % x == m2```.
* Improve the code by removing one level of nestednees, i.e. change ```if x % 17 == m1``` to ```if x % 17 != m1``` and use ```continue```.
* Use debugger to check how the code works.

In [0]:
X = [19, 4, 11, 14, 9, 20, 3, 9, 20, 13, 12, 18, 5, 19, 20, 1, 7, 15, 18, 17]
Y = [69, 56, 91, 77, 63, 86, 86, 53, 63, 100, 82, 54, 69, 92, 55, 85, 54, 79, 98, 68]

m1 = 1
m2 = 7

result = []
for x in X:
  if x % 17 == m1:
    for y in Y:
      if y % x == m2:
        result.append([x, y])

print(result)

##Break

**Problem:** Implement linear search in a list. Given an unsorted list L, check whether it contains certain predefined number x. Print "found" if yes and "no such number" otherwise. To use Python syntax effectively, consider the full form of the ```for``` cycle
```python
for <some statements>:
  <doing something here>
  <possibly break>
else:
  <do if no break occured>
```
Print "found" and break if you located the number; print "no such number" in the ```else``` block. Use debugger to understand how your final code works.

**Note:** this ```else``` block belongs to the **cycle**, not some "hidden if". It is a Python's feature to have ```else``` blocks for cycles, though rarely used.


In [0]:
L = [15, 2, 12, 6, 11, 16, 1, 12, 18, 15, 7, 2, 4, 2, 14, 13, 2, 16, 16, 16]
x = 18 # Experiment with different x-s

# Enter your code here

##Functions

**Problem:** 
* Write function ```like_set``` that makes a list look like a set, i.e. removes all duplicates
* Write $3$ set-theoretic functions:
  - ```union``` -- takes two lists of elements (mimicing sets) and returns their union, i.e. list that contains all elements present in the given lists but with no repetition.
  - ```intersection``` -- takes two lists of elements (mimicing sets) and returns their intersection, i.e. all elements that given lists have in common
  - ```complement``` -- takes two lists of elements (first mimics set, second -- universum) and returns list of elements present in the second set but not in the first one.
* Test on a given example that completion of union is intersection of completions (de Morgan's law) $(A \cup B)^c = A^c \cap B^c$ and distributive law $A \cap(B \cup C) = (A \cap B) \cup (A \cap C)$.

**Note:** you can use debugger intensively (add ``%%debug_cell_with_pytutor`` at the top of the cell).

In [0]:

# Enter your code here


# This is test part
# See how functions are ment to be used here

X = [1, 2, 3, 4, 5, 6, 7, 8, 9] # Universum
A = [1, 3, 5]                   # set A
B = [2, 3, 5, 7, 9]             # set B
C = [1, 5, 8]                   # set C

# Following assertions will fail if your implementation performs poorly

assert sorted(intersection(A, B)) == [3, 5]
assert sorted(union(B, C)) == [1, 2, 3, 5, 7, 8, 9]
assert sorted(complement(union(A, B), X)) == sorted(intersection(complement(A, X), complement(B, X)))

###Solution
If you feel totally stuck, you may check the following solution. But I strongly advise you not to do so unless you spent at least 10 minutes solving this problem

In [0]:
%%debug_cell_with_pytutor

def like_set(l):
  res = []
  for x in l1:
    if not x in res:
      res.append(x)

def intersection(l1, l2):
  res = []
  for x in l1:
    if x in l2:
        res.append(x)
  return res

def union(l1, l2):
  res = l1.copy()
  for x in l2:
    if not x in res:
        res.append(x)
  return res

def complement(l, X):
  res = []
  for x in X:
    if not x in l:
        res.append(x)
  return res


X = [1, 2, 3, 4, 5, 6, 7, 8, 9] # Universum
A = [1, 3, 5]                   # set A
B = [2, 3, 5, 7, 9]             # set B
C = [1, 5, 8]                   # set C

assert sorted(intersection(A, B)) == [3, 5]
assert sorted(union(B, C)) == [1, 2, 3, 5, 7, 8, 9]
assert sorted(complement(union(A, B), X)) == sorted(intersection(complement(A, X), complement(B, X)))

##Modules

**Problem:** 
* Consider the following code. Make sure you understand how modules are imported. Consider the functions used and make sure you understand what they do (this functions are often used, thus they are valuable on their own).
* Change the code so that there is no need to wirte module name when calling a function, i.e. we should be able to write ```sin``` instead of ```math.sin```.

**Note:** you can use debugger intensively (add ``%%debug_cell_with_pytutor`` at the top of the cell).

In [0]:
# Simple built-ins
print(pow(2, 4), 2 ** 4)
print(abs(-42.0), sum((1, 2, 3, 4)))
print(min(3, 1, 2, 4), max(3, 1, 2, 4))

# The math module
import math

print(math.pi, math.e)
print(math.sin(2 * math.pi / 180))
print(math.sqrt(144), math.sqrt(2))

# rounding
print(math.floor(2.567), math.floor(-2.567))
print(math.trunc(2.567), math.trunc(-2.567))

# compare to
print(int(2.567), int(-2.567))
print(round(2.567), round(2.467), round(2.567, 2))
print('%.1f' % 2.567, '{0:.2f}'.format(2.567))

# The random module
import random

print(random.random())
print(random.random())
print(random.randint(1, 10))
print(random.randint(1, 10))
print(random.choice(['ML', 'theoretical Physics', 'Biochemistry']))
print(random.choice(['ML', 'theoretical Physics', 'Biochemistry']))

##Local vs Global

**Problem:** 
* Consider the following code and understand how ```global``` keyword works. 
* Remove the line ```global x``` and look what happens.

**Note:** using globals is not a good practice, but sometimes unavoidable.

In [0]:
%%debug_cell_with_pytutor

y, z = 1, 2         # global variables in module
def all_global():
  global x        # declare globals assigned
  x = y + z       # no need to declare y,z: 3-scope rule

all_global()  
print(x)  

**Problem:** 
* Consider the following code and understand how function can return a function
* Consider the following code and understand how ```nonlocal``` keyword works. 
* Remove the line ```nonlocal x``` and look what happens.

**Note:** creting function inside function and returning it is a feature of functional programming style. Though Python is not Haskell, it allows you to use functional style. I have rarely seen this style in industrial programming and it really takes some time to get used, thus you may skip this problem if you feel it is sort of "black magic".

In [0]:
%%debug_cell_with_pytutor

def outer():
  x = 1
  def inner():
    nonlocal x
    x += 1
    print(x)
  return inner

f = outer()      # f is really an inner

f()
f()

##Classes

**Problem:** Consider the following very basic example of class. Experiment with this code until you cleaarly understand the difference between *class* and *object*. You should understand how objects are created and than used in Python.

In [0]:
%%debug_cell_with_pytutor

class FirstClass: # define a class object
  def setdata(self, value): # define class methods
    self.data = value # self is the instance
 
  def display(self):
    print(self.data) # self.data: per instance

    
x = FirstClass() # make two instances
y = FirstClass() # each is a new namespace
 
x.setdata("King Arthur") # call methods
y.setdata(3.14159)
 

x.display() # self.data differs in each
y.display()

x.data = "New value" # can get/set attributes
x.display() # outside the class too

##Scopes

**Problem:** Consider the following code and understand how different scopes in Python interact. 

In [0]:
%%debug_cell_with_pytutor

# all 5 Xs are different variables
X = 1 # global
 
def f():
  X = 2 # local

class C:
  X = 3 # class
  
  def m(self):
    X = 4 # local
    self.X = 5 # instance

f()
c = C()
c.m()

#Learn to solve following problems

First, read through the problem. 
You will mostly be asked to implement some missing parts of code. 
Please, do not use `numpy` or any fancy libraries at this stage -- we will need to convert your code to JS later.

**Problem:**
* Implement missing parts of code according to instructions in comments
* Make sure your code passes unit-tests, e.g. start the cell and observe if any assert fails
* Uncomment the top-most line ```%%embed_into_game walker```, start the cell and observe the result. If you can see a field with red square, click a mouse on it to activate the output cell and try moving this block with ```w,a,s,d``` keys.
* Do not use any additional libraries except the ones I have already imported for you (this code will be cross-compiled to JS, thus only a scarce number of libraries is available).

In [0]:
%%embed_into_game walker

class Walker:
  def __init__(self, x, y, w, h):
    # Implement constructor
    # x and y are initial coordinates of the walker
    # w and h are the size of the field
    # make the object "remember" this parameters --
    # save them to private variables

  def step(self, dx, dy):
    # Implement a walking function.
    # Walker should do a step,
    # i.e. add dx to its current x
    # and add dy to its current y.
    # Make sure walker will not fall of the field!
    # If x should always remain 0 <= x < w
    # and y should always remain 0 <= y < h

  def get_position(self):
    # Return position of the Walker.
    # Use tuple return to return x and y simultaneously


walker = Walker(1, 1, 3, 3)
assert isinstance(walker, Walker), "Not instance of Walker"
assert (1,1) == walker.get_position(), "Wrong position"
walker.step(1,0)
assert (2,1) == walker.get_position(), "Wrong positionafter step"
walker.step(1,0)
assert (2,1) == walker.get_position(), "Edge cases not handled"
print("ALL TESTS SUCCESSFULLY PASSED")

#Recreational Python

You should solve the following is series of problems one-by-one (every next problem is based on the solution of the previous). We will start with a few simple classes and develop a small game throughout this excercise. Hope, you'll enjoy it.

**Note:** you can still use `%%debug_cell_with_pytutor` for debugging as in previous examples, but don't forget to remove this line after debug is finished.

##Problem 1

Implement a very simple class `vector2D` and a function `clamp`. I expect you to implement the following:

* `__init__` -- a constructor. You should save two given values (`x` and `y`) to attributes `x` and `y`. I expect this atttributes to be accessible later
* `__add__` -- you should implement addition of two vectors -- `self` and `other`
* `__sub__` -- you should implement subtraction of two vectors -- `self` and `other`
* `__mul__` -- you should implement multiplication of vector `self` by number `num`
* `__rmul__` -- implemented for you
* function `clamp(x, x_min, x_max)` -- should return `x_min` if `x < x_min`; `x_max` if `x > m_max` and `x` otherwise

You can test your code with unittests I have provided.

In [0]:
class Vector2D:
  def __init__(self, x=0, y=0): 
    pass # Remove 'pass' and enter your code here
  def __add__(self, other): 
    pass # Remove 'pass' and enter your code here
  def __sub__(self, other): 
    pass # Remove 'pass' and enter your code here
  def __mul__(self, num): 
    pass # Remove 'pass' and enter your code here
  def __rmul__(self, other): return self.__mul__(other)

def clamp(x, x_min, x_max):
  pass # Remove 'pass' and enter your code here


# The following code tests your implementation
# Make sure your code passes tests before moving to the next problem
v = Vector2D(1, 2)
assert isinstance(v, Vector2D), "Not instance of Vector2D"
assert v.x == 1 and v.y == 2, "Attribute 'x' or 'y' is incorrect"
u = 3 * v
w = v * 5
assert u.x == 3 and u.y == 6 and w.x == 5 and w.y == 10, "Wrong multilication"
s = u + w
assert s.x == 8 and s.y == 16, "Wrong addition"
v = w - u
assert v.x == 2 and v.y == 4, "Wrong subtraction"

assert clamp(1, 3, 7) == 3, "clamp lower bound error"
assert clamp(5, 3, 7) == 5, "clamp intermediate error"
assert clamp(14, 3, 7) == 7, "clamp upper bound error"

print("ALL TESTS SUCCESSFULLY PASSED")

ALL TESTS SUCCESSFULLY PASSED


###Solution

In [0]:
class Vector2D:
  def __init__(self, x=0, y=0): self.x, self.y = x, y
  def __add__(self, other): return Vector2D(self.x + other.x, self.y + other.y)
  def __sub__(self, other): return Vector2D(self.x - other.x, self.y - other.y)
  def __mul__(self, num): return Vector2D(self.x * num, self.y * num)
  def __rmul__(self, other): return self.__mul__(other)

def clamp(x, x_min, x_max):
  if x < x_min: return x_min
  if x > x_max: return x_max
  return x

##Problem 2

**Part A**

* Copy your implementations of `Vector2D` and `clamp` 
* Implement missing functions in class `Ball`
   - `__init__(self, r, color, p, v, g)` -- constructor; it is given a bunch of data that you should save to internal variables:
       + `r` -- ball radius, integer
       + `color` -- ball color, string, e.g. 'green', 'red', 'blue'
       + `p` -- `Vector2D` that contains current coordinates
       + `v` -- `Vector2D`, velocity of the ball
       + `g` -- float number, gravity
   - `get_coordinates(self)` -- return a `Vector2D` that contains current coordinates of the ball
   - `get_properties(self)` -- return a float (ball radius) and a string (ball color); use multiple return feature to implement this function
   - `move_and_view` -- imlement ball movement. You may suppose the time is dimensionless. I expect you to calculate current position $\vec{p}_{i+1}$ ($i$ is the iteration number) as
   $$
   \vec{p}_{i+1} = \vec{p}_{i} + \vec{v}_i,
   $$
   update velocity
   $$
   \vec{v}_{i+1} = \vec{v}_{i} - g \vec{e}_y
   $$
   and clamp velocity to prevent it from overgroving. Make sure that for any iteration it is true that
   $$
   \begin{aligned}
   -\frac{r}{2} < \vec{v}_x < \frac{r}{2},\\
   -\frac{r}{2} < \vec{v}_y < \frac{r}{2}.
   \end{aligned}
   $$
   Function `clamp` applied to x and y components will be helpful.
* Make sure all tests are passing

**Part B**

  
* Implement `wait_for_key_and_start()` function. This function is an entry point. Create a **global** object `ball` of class `Ball` here (use the keyword `global` to make it global). Use parameters
   - radius `10`
   - color `'red'`
   - initial position `Vector2D(total_w/2, total_h/2)`
   - initial velocity `Vector2D(1, 1)`
   - gravity constant `0.01`
* Implement `timer_tick(key_left, key_right)`. You just need to call method `move_and_view()` of the object `ball`, ignore everything else.  
* Uncomment `%%embed_into_game ball` at the top of the cell. Start code and see the moving ball. Fix errors if any occurs

**Part C**

* Modify the `timer_tick` function -- check position of the ball at every step (`get_coordinates` function shoul be helpful), if the ball falls off the field, i.e. its coordinates become negative or larger than `total_w` and `total_h` --  call `publish_message('ENTER to restart')` and than `wait_for_key_and_start()`.

In [0]:
#%%embed_into_game ball

import math
import random

total_w = 1000
total_h = 600


class Vector2D: pass
  # copy your code from previous example here

def clamp(x, x_min, x_max): pass
  # copy your code from previous example here


class Ball:
  def __init__(self, r, color, p, v, g):
    pass # Remove 'pass' and enter your code here
  
  def get_coordinates(self):
    pass # Remove 'pass' and enter your code here

  def get_properties(self): 
    pass # Remove 'pass' and enter your code here

  def move_and_view(self):
    pass # Remove 'pass' and enter your code here 

# This function will be called on timer
# It should perform one step of evolution 
# Update positon ob the ball here
def timer_tick(key_left, key_right):
  pass # Remove 'pass' and enter your code here

def wait_for_key_and_start():
  pass # Remove 'pass' and enter your code here

  
def publish_message(msg):
  print(msg)

wait_for_key_and_start()

#### TESTS ######
# The following code tests your implementation
# Make sure your code passes tests before moving to the next problem
ball = Ball(15, 'green', Vector2D(10, 15), Vector2D(-1, 1), 0.0)
assert isinstance(ball, Ball), "Not an instance of Ball"
p = ball.get_coordinates()
assert p.x == 10 and p.y == 15, "Coordinates not set properly"
ball.move_and_view()
p = ball.get_coordinates()
assert p.x == 9 and p.y == 16, "Moves incorrectly"
r, c = ball.get_properties()
assert r == 15 and c == 'green', "Properties are wrong"
ball = Ball(2, 'green', Vector2D(0, 0), Vector2D(1, -1), 10.0)
for _ in range(100):
  ball.move_and_view()
p = ball.get_coordinates()
assert 99 < p.x < 101 and -101 < p.y < -99, "Velocity not clamped"
print("TESTS PASSED")

###Solution

In [0]:
%%embed_into_game ball

import math
import random

total_w = 1000
total_h = 600


class Vector2D:
  def __init__(self, x=0, y=0): self.x, self.y = x, y
  def __add__(self, other): return Vector2D(self.x + other.x, self.y + other.y)
  def __sub__(self, other): return Vector2D(self.x - other.x, self.y - other.y)
  def __mul__(self, num): return Vector2D(self.x * num, self.y * num)
  def __rmul__(self, other): return self.__mul__(other)

def clamp(x, x_min, x_max):
  if x < x_min: return x_min
  if x > x_max: return x_max
  return x

class Ball:
  def __init__(self, r, color, p, v, g):
    self.r, self.color = r, color
    self.p, self.v, self.g = p, v, g

  # do not change the signature of this methods
  # it is needed for correct drawing
  def get_coordinates(self): return self.p
  def get_properties(self): return self.r, self.color

  def move_and_view(self):
    self.p += self.v
    self.v.y -= self.g
    self.v = Vector2D(clamp(self.v.x, -self.r/2, self.r/2), clamp(self.v.y, -self.r/2, self.r/2)) 


# This function will be called on timer
# It should perform one step of evolution 
# Update positon of the ball here
def timer_tick(key_left, key_right):
  ball.move_and_view()
  p = ball.get_coordinates()
  if p.x < 0 or p.x > total_w or p.y < 0 or p.y > total_h:
    publish_message('ENTER to restart')
    wait_for_key_and_start()

def wait_for_key_and_start():
  global ball
  ball = Ball(10, 'red', Vector2D(total_w/2, total_h/2), Vector2D(1, 1), 0.01)

def publish_message(msg):
  print(msg)

wait_for_key_and_start()

##Problem 3

Now we will endow the ball with the ability to bounce. 
Basically, we need only one function, but you may find it a bit challenging.
Feel free to see the solution if you are stuck for more then 15 minutes.

**Part A**
* Copy your implementations from the previous problem
* Implement `collide(self, u, v)` function. As an input function takes two parameters `u` and `v` both of type `Vector2D`. These are the endpoints of certain segment you should bounce the ball off. You may (and for the sake of simplicity you better do) **suppose that the segment is either horizontal or vertical**. Basically, your implementation should contain two logical parts: detect the bouncing and change ball's velocity.
    - Coordinates. Change coordinate system to more convenient, i.e. if you subtract `(v+u) * 0.5` from `v`, `u`, and `self.p`, you will end up with a segment spanning -d to d along X or Y axes (assuming that the segment is either horizontal or vertical).
    - Detection. Suppose, the ball has coordinates \\(\vec{p}\\)
    in the new coordinate system and one of the segment's ends has coordinates \\(\vec{s}\\). If the segment is vertical, you consider the ball bouncing if $|p_y| < |s_y|$ and $|p_x| < r$, where $r$ is the ball's radius. Analogous equations hold for horizontal segment.
    - Bouncing. If you have detected that the ball should bounce -- modify its velocity. You should check that the sign of the appropriate velocity component coincides with the sing of new coordinate. As an example. Consider bouncing off the vertical segment. If $p_x > 0$ you should make $v_x > 0$ (and keeping its magnitude), if $p_x < 0$ you should make $v_x < 0$ (and keep its magnitude intact).
    - Return value. I expect your function to return `True` if the ball has bounced and `False` otherwise. 
* Make sure that tests are passing. You can use `%%debug_cell_with_pytutor` to make your debug easier.

**Note:** you may have noticed that for large velocities ball will tunnel through the wall (how quantum mechanically, I should say :) ). This is the reason, why I asked you to limit its speed in the previous problem. If you have ignored this part of the instructions, it's time to implement it. Or you may come up with some more robust and cunning algorithm for bouncing -- let me know and I will consider it for the future runs of the course.

**Part B**
* Implement `timer_tick`. First of all, you should call `move_and_view` on every tick. Moreover, now you need to call `collide` to make ball bounve off the walls. Consider the following segment endpoints:
    - From `Vector2D(0, 0)` to `Vector2D(0, total_h)` -- left wall
    - From `Vector2D(total_w, 0)` to `Vector2D(total_w, total_h)` -- right wall
    - From `Vector2D(total_w, 0)` to `Vector2D(0, 0)` -- bottom
    - From `Vector2D(total_w, total_h)` to `Vector2D(0, total_h)` -- top
* Uncomment `%%embed_into_game ball` at the top of the cell. Start code and see the moving ball. Fix errors if any occurs.



In [0]:
#%%embed_into_game ball

import math
import random

total_w = 1000
total_h = 600


class Vector2D:
  # copy your code from the previous problem here

def clamp(x, x_min, x_max):
  # copy your code from the previous problem here

class Ball:
  def __init__(self, r, color, p, v, g):
    # copy your code from the previous problem here

  def get_coordinates(self): 
    # copy your code from the previous problem here

  def get_properties(self): 
    # copy your code from the previous problem here

  def move_and_view(self):
    # copy your code from the previous problem here 

  def collide(self, v, u):
    pass # Remove 'pass' and enter your code here


# This function will be called on timer
# It should perform one step of evolution 
# Update positon of the ball here
def timer_tick(key_left, key_right):
  pass # Remove 'pass' and enter your code here

def wait_for_key_and_start():
  # copy your code from the previous problem here

def publish_message(msg):
  print(msg)

wait_for_key_and_start()


### TESTS #####
b = Ball(10, 'red', Vector2D(10, 0), Vector2D(5, 0), 0.0)
was_collision = False
for _ in range(10):
  b.move_and_view()
  if b.collide(Vector2D(25, 10), Vector2D(25, -10)): was_collision = True
if not was_collision:
  assert False, "No collision reported (function should have return true at some point)"
p = b.get_coordinates()
assert p.y == 0, "y coordinate should not change during x-bounce"
assert p.x < 0, "did not bounce (vertical, bounce from the left)"

b = Ball(10, 'red', Vector2D(-10, 0), Vector2D(-5, 0), 0.0)
was_collision = False
for _ in range(10):
  b.move_and_view()
  if b.collide(Vector2D(-25, 10), Vector2D(-25, -10)): was_collision = True
if not was_collision:
  assert False, "No collision reported (function should have return true at some point)"
p = b.get_coordinates()
assert p.y == 0, "y coordinate should not change during x-bounce"
assert p.x > 0, "did not bounce (vertical, bounce from the right)"

b = Ball(10, 'red', Vector2D(0,10), Vector2D(0,5), 0.0)
was_collision = False
for _ in range(10):
  b.move_and_view()
  if b.collide(Vector2D(10, 25), Vector2D(-10, 25)): was_collision = True
if not was_collision:
  assert False, "No collision reported (function should have return true at some point)"
p = b.get_coordinates()
assert p.x == 0, "x coordinate should not change during y-bounce"
assert p.y < 0, "did not bounce (horizontal, bounce from below)"

b = Ball(10, 'red', Vector2D(0,-10), Vector2D(0,-5), 0.0)
was_collision = False
for _ in range(10):
  b.move_and_view()
  if b.collide(Vector2D(10, -25), Vector2D(-10, -25)): was_collision = True
if not was_collision:
  assert False, "No collision reported (function should have return true at some point)"
p = b.get_coordinates()
assert p.x == 0, "x coordinate should not change during y-bounce"
assert p.y > 0, "did not bounce (horizontal, bounce from above)"

print("TESTS PASSED")

###Solution

In [0]:
%%embed_into_game ball

import math
import random

total_w = 1000
total_h = 600


class Vector2D:
  def __init__(self, x=0, y=0): self.x, self.y = x, y
  def __add__(self, other): return Vector2D(self.x + other.x, self.y + other.y)
  def __sub__(self, other): return Vector2D(self.x - other.x, self.y - other.y)
  def __mul__(self, num): return Vector2D(self.x * num, self.y * num)
  def __rmul__(self, other): return self.__mul__(other)

def clamp(x, x_min, x_max):
  if x < x_min: return x_min
  if x > x_max: return x_max
  return x

class Ball:
  def __init__(self, r, color, p, v, g):
    self.r, self.color = r, color
    self.p, self.v, self.g = p, v, g

  def get_coordinates(self): return self.p
  def get_properties(self): return self.r, self.color

  def move_and_view(self):
    self.p += self.v
    self.v.y -= self.g
    self.v = Vector2D(clamp(self.v.x, -self.r/2, self.r/2), clamp(self.v.y, -self.r/2, self.r/2)) 

  def collide(self, v, u):
    d = u - (v + u) * 0.5
    p = self.p - (v + u) * 0.5
    if ((abs(p.y) < abs(d.y)) and (abs(p.x) < self.r)):
      self.v.x *= (2*(p.x * self.v.x >= 0) - 1)
      return True
    if ((abs(p.x) < abs(d.x)) and (abs(p.y) < self.r)):
      self.v.y *= (2*(p.y * self.v.y >= 0) - 1)
      return True
    return False


# This function will be called on timer
# It should perform one step of evolution 
# Update positon of the ball here
def timer_tick(key_left, key_right):
  ball.move_and_view()
  ball.collide(Vector2D(0, 0), Vector2D(0, total_h))
  ball.collide(Vector2D(total_w, 0), Vector2D(total_w, total_h))
  ball.collide(Vector2D(total_w, 0), Vector2D(0, 0))
  ball.collide(Vector2D(total_w, total_h), Vector2D(0, total_h))

def wait_for_key_and_start():
  global ball
  ball = Ball(10, 'red', Vector2D(total_w/2, total_h/2), Vector2D(1, 1), 0.01)

def publish_message(msg):
  print(msg)

wait_for_key_and_start()


### TESTS #####
b = Ball(10, 'red', Vector2D(10, 0), Vector2D(5, 0), 0.0)
was_collision = False
for _ in range(10):
  b.move_and_view()
  if b.collide(Vector2D(25, 10), Vector2D(25, -10)): was_collision = True
if not was_collision:
  assert False, "No collision reported (function should have return true at some point)"
p = b.get_coordinates()
assert p.y == 0, "y coordinate should not change during x-bounce"
assert p.x < 0, "did not bounce (vertical, bounce from the left)"

b = Ball(10, 'red', Vector2D(-10, 0), Vector2D(-5, 0), 0.0)
was_collision = False
for _ in range(10):
  b.move_and_view()
  if b.collide(Vector2D(-25, 10), Vector2D(-25, -10)): was_collision = True
if not was_collision:
  assert False, "No collision reported (function should have return true at some point)"
p = b.get_coordinates()
assert p.y == 0, "y coordinate should not change during x-bounce"
assert p.x > 0, "did not bounce (vertical, bounce from the right)"

b = Ball(10, 'red', Vector2D(0,10), Vector2D(0,5), 0.0)
was_collision = False
for _ in range(10):
  b.move_and_view()
  if b.collide(Vector2D(10, 25), Vector2D(-10, 25)): was_collision = True
if not was_collision:
  assert False, "No collision reported (function should have return true at some point)"
p = b.get_coordinates()
assert p.x == 0, "x coordinate should not change during y-bounce"
assert p.y < 0, "did not bounce (horizontal, bounce from below)"

b = Ball(10, 'red', Vector2D(0,-10), Vector2D(0,-5), 0.0)
was_collision = False
for _ in range(10):
  b.move_and_view()
  if b.collide(Vector2D(10, -25), Vector2D(-10, -25)): was_collision = True
if not was_collision:
  assert False, "No collision reported (function should have return true at some point)"
p = b.get_coordinates()
assert p.x == 0, "x coordinate should not change during y-bounce"
assert p.y > 0, "did not bounce (horizontal, bounce from above)"

print("TESTS PASSED")

##Problem 4

Now we add a new object to interact with -- a block.

**Part A**
* Copy your implementations from the previous problem
* Implement a class `Block`. I have already created a draft, you should complete implementation of few function here.
   - `__init__(self, p, size, color="blue", v=0.0, direction=Vector2D(0, 0))` -- constructor; it is given a bunch of data that you should store to internal variables:
       + `p` -- `Vector2D`, contains current coordinates (corresponds to the lower left corner)
       + `size` -- `Vector2D`, contains width and height of the block
       + `color` -- block color, string, e.g. 'green', 'red', 'blue'
       + `v` -- float number, absolute value of the velocity of the ball (not a vector!) velocity of the ball
       + `direction` -- `Vector2D`, unit vector along direction of movement; velocity as a vector should be `v * direction`
   - `get_sizes` -- should return two `Vector2D` -- coordinate of the block (initial is `p`) and its size; use multiple return feature to implement this function
   - `get_properties` -- should return one string -- color of the block
   - `move_and_view` -- change position of the block by `v * direction`, clamp coordinates so that the block remains inside the field
* Make sure that tests pass

**Part B**
* Explore the `timer_tick` and `wait_for_key_and_start` functions -- I have created an arrangement of few blocks for you. Make sure you understand how it is intended to work.
* Uncomment `%%embed_into_game ball` at the top of the cell. Start code and see the moving ball. Ball will pass through blocks (that's ok for this part)
* Make ball and blocks collide. You need to implement function `collide_ball_block(ball, block)`. In this function you need to take position and size of the `block` and radius of the `ball`. Then call `ball.collide` with each side of the block. 
* Collision with block's corner allows the ball to sneak into the block. Fix this problem by extending segments it collides with by `r/2` (half of ball's radius), i.e. collision with bottom of the block should be described as collision with segment from `Vector2D(p.x - r/2, p.y)` to `Vector2D(p.x + size.x + r/2, p.y)`, where `p` and `size` are block's position and size.
* Run your code and make sure ball now collides with blocks.

In [0]:
#%%embed_into_game ball

import math
import random

total_w = 1000
total_h = 600


class Vector2D:
  # copy your code from previous example here

def clamp(x, x_min, x_max):
  # copy your code from previous example here

class Ball:
  def __init__(self, r, color, p, v, g):
    # copy your code from previous example here

  def get_coordinates(self):
    # copy your code from previous example here

  def get_properties(self):
    # copy your code from previous example here

  def move_and_view(self):
    # copy your code from previous example here

  def collide(self, v, u):
    # copy your code from previous example here

class Block:
  def __init__(self, p, size, color="blue", v=0.0, direction=Vector2D(0, 0)):
    pass # Remove 'pass' and enter your code here

  def move_and_view(self):
    pass # Remove 'pass' and enter your code here

  def get_sizes(self): 
    pass # Remove 'pass' and enter your code here

  def get_properties(self):
    pass # Remove 'pass' and enter your code here

def collide_ball_block(ball, block):
  pass # Remove 'pass' and enter your code here

# This function will be called on timer
# It should perform one step of evolution 
# Update positon ob the ball here
def timer_tick(key_left, key_right):
  for ball in balls:
    ball.move_and_view()
    ball.collide(Vector2D(0, 0), Vector2D(0, total_h))
    ball.collide(Vector2D(total_w, 0), Vector2D(total_w, total_h))
    ball.collide(Vector2D(total_w, 0), Vector2D(0, 0))
    ball.collide(Vector2D(total_w, total_h), Vector2D(0, total_h))
    for b in blocks:
      b.move_and_view()
      collide_ball_block(ball, b)


def wait_for_key_and_start():
  global balls, blocks
  balls = [Ball(10, 'red', Vector2D(300, 400), Vector2D(3, -3), 0.0),
           Ball(10, 'green', Vector2D(700, 200), Vector2D(-3, 3), 0.0),
           Ball(10, 'yellow', Vector2D(400, 100), Vector2D(3, 3), 0.0),
           Ball(10, 'orange', Vector2D(600, 500), Vector2D(-3, -3), 0.0)]

  blocks = [Block(Vector2D(400, 200), Vector2D(200, 200)),
            Block(Vector2D(100, 100), Vector2D(100, 100)),
            Block(Vector2D(100, 400), Vector2D(100, 100)),
            Block(Vector2D(800, 100), Vector2D(100, 100)),
            Block(Vector2D(800, 400), Vector2D(100, 100))]

def publish_message(msg):
  print(msg)

wait_for_key_and_start()

#### TESTS ######
# The following code tests your implementation
# Make sure your code passes tests before moving to the next problem
block = Block(Vector2D(400, 200), Vector2D(200, 200), 'green', 100, Vector2D(-1, 1))
assert isinstance(block, Block), "Not an instance of Block"
p, sz = block.get_sizes()
assert p.x == 400 and p.y == 200, "Coordinates not set properly"
assert sz.x == 200 and sz.y == 200, "Width/Height not set properly"
c = block.get_properties()
assert c == 'green', "Properties are wrong"
block.move_and_view()
p, sz = block.get_sizes()
assert p.x == 300 and p.y == 300, "Coordinates not set properly"
assert sz.x == 200 and sz.y == 200, "Width/Height not set properly"
print("TESTS PASSED")

###Solution

In [0]:
%%embed_into_game ball

import math
import random

total_w = 1000
total_h = 600


class Vector2D:
  def __init__(self, x=0, y=0): self.x, self.y = x, y
  def __add__(self, other): return Vector2D(self.x + other.x, self.y + other.y)
  def __sub__(self, other): return Vector2D(self.x - other.x, self.y - other.y)
  def __mul__(self, num): return Vector2D(self.x * num, self.y * num)
  def __rmul__(self, other): return self.__mul__(other)

def clamp(x, x_min, x_max):
  if x < x_min: return x_min
  if x > x_max: return x_max
  return x

class Ball:
  def __init__(self, r, color, p, v, g):
    self.r, self.color = r, color
    self.p, self.v, self.g = p, v, g

  # do not change the signature of this methods
  # it is needed for correct drawing
  def get_coordinates(self): return self.p
  def get_properties(self): return self.r, self.color

  def move_and_view(self):
    self.p += self.v
    self.v.y -= self.g
    self.v = Vector2D(clamp(self.v.x, -self.r/2, self.r/2), clamp(self.v.y, -self.r/2, self.r/2)) 

  def collide(self, v, u):
    d = u - (v + u) * 0.5
    p = self.p - (v + u) * 0.5
    if ((abs(p.y) < abs(d.y)) and (abs(p.x) < self.r)):
      self.v.x *= (2*(p.x * self.v.x >= 0) - 1)
      return True
    if ((abs(p.x) < abs(d.x)) and (abs(p.y) < self.r)):
      self.v.y *= (2*(p.y * self.v.y >= 0) - 1)
      return True
    return False

class Block:
  def __init__(self, p, size, color="blue", v=0.0, direction=Vector2D(0, 0)):
    self.p, self.size, self.color, self.v = p, size, color, v
    self.direction = direction

  def move_and_view(self):
    self.p += self.v * self.direction
    self.p = Vector2D(clamp(self.p.x, 0, total_w - self.size.x), clamp(self.p.y, 0, total_h - self.size.y))

  def get_sizes(self): return self.p, self.size
  def get_properties(self): return self.color

def collide_ball_block(ball, block):
  p, size = block.get_sizes()
  r, _ = ball.get_properties()
  sides = [[Vector2D(p.x - r/2, p.y), Vector2D(p.x + size.x + r/2, p.y)],
           [Vector2D(p.x, p.y - r/2), Vector2D(p.x, p.y + size.y + r/2)],
           [Vector2D(p.x + size.x, p.y - r/2), Vector2D(p.x + size.x, p.y + size.y + r/2)],
           [Vector2D(p.x + size.x + r/2, p.y + size.y), Vector2D(p.x - r/2, p.y + size.y)]]
  for p1, p2 in sides:
    if ball.collide(p1, p2):
      return True
  return False

# This function will be called on timer
# It should perform one step of evolution 
# Update positon ob the ball here
def timer_tick(key_left, key_right):
  for ball in balls:
    ball.move_and_view()
    ball.collide(Vector2D(0, 0), Vector2D(0, total_h))
    ball.collide(Vector2D(total_w, 0), Vector2D(total_w, total_h))
    ball.collide(Vector2D(total_w, 0), Vector2D(0, 0))
    ball.collide(Vector2D(total_w, total_h), Vector2D(0, total_h))
    for b in blocks:
      b.move_and_view()
      collide_ball_block(ball, b)


def wait_for_key_and_start():
  global balls, blocks
  balls = [Ball(10, 'red', Vector2D(300, 400), Vector2D(3, -3), 0.0),
           Ball(10, 'green', Vector2D(700, 200), Vector2D(-3, 3), 0.0),
           Ball(10, 'yellow', Vector2D(400, 100), Vector2D(3, 3), 0.0),
           Ball(10, 'orange', Vector2D(600, 500), Vector2D(-3, -3), 0.0)]

  blocks = [Block(Vector2D(400, 200), Vector2D(200, 200)),
            Block(Vector2D(100, 100), Vector2D(100, 100)),
            Block(Vector2D(100, 400), Vector2D(100, 100)),
            Block(Vector2D(800, 100), Vector2D(100, 100)),
            Block(Vector2D(800, 400), Vector2D(100, 100))]

def publish_message(msg):
  print(msg)

wait_for_key_and_start()

#### TESTS ######
# The following code tests your implementation
# Make sure your code passes tests before moving to the next problem
block = Block(Vector2D(400, 200), Vector2D(200, 200), 'green', 100, Vector2D(-1, 1))
assert isinstance(block, Block), "Not an instance of Block"
p, sz = block.get_sizes()
assert p.x == 400 and p.y == 200, "Coordinates not set properly"
assert sz.x == 200 and sz.y == 200, "Width/Height not set properly"
c = block.get_properties()
assert c == 'green', "Properties are wrong"
block.move_and_view()
p, sz = block.get_sizes()
assert p.x == 300 and p.y == 300, "Coordinates not set properly"
assert sz.x == 200 and sz.y == 200, "Width/Height not set properly"
print("TESTS PASSED")

##Problem 5

Now is time to implement a real game -- let's do a simple ping-pong.
We already have all parts of the jigsaw, we only need to put them together.

**Part A**
* Copy your implementations from the previous problem
* Create two rackets in function `wait_for_key_and_start`. Class `Block` will be helpful. Set their positions as `Vector2D(total_w/2 - 100, 5)` and `Vector2D(total_w/2 - 100, total_h - 20)`, use size `Vector2D(200, 15)` and velocity `5.0`. You might want to endow them with different colors.
* Call `move_and_view` for each racket in the `timer_tick` function. Run your code and make sure that rackets are drawn.

**Part B**
* Implement function `set_direction` in class `Block`. It should take `Vector2D` that contains new direction and update the appropriate internal variable.
* Now consider arguments of `timer_tick(key_left, key_right)`. This function gets status of keys for two players `key_left` for one player and `key_right` for another. Call the `set_direction` function for each racket to make them move. Keys are decoded as follows
   - If `key_left` is equal to -1 -- left player presses 'z' button -- set direction to `Vector2D(-1, 0)`
   - If `key_left` is equal to 1 -- left player presses 'x' button -- set direction to `Vector2D(1, 0)`
   - If `key_left` is equal to 0 -- left player does not press any key -- set direction to `Vector2D(0, 0)`
   - If `key_right` is equal to -1 -- right player presses '<' button -- set direction to `Vector2D(-1, 0)`
   - If `key_right` is equal to 1 -- right player presses '>' button -- set direction to `Vector2D(1, 0)`
   - If `key_right` is equal to 0 -- right player does not press any key -- set direction to `Vector2D(0, 0)`
* Run your code and make sure the rackets are moving as expected.


**Part C**
* Modify `wait_for_key_and_start`. You should additionally create a ball there. Set its radius to 10, position the ball at `Vector2D(total_w/2, total_h/2)` and set its initial velocity as `Vector2D(1, 1)`.
* Modify `timer_tick` function -- make sure that you are calling `ball.collide` with all 4 field borders (see previous problem if needed) and that you call `collide_ball_block` with two rackets.
* Start your code and make sure the ball bounces as needed.


**Part D**
* In class `Block` implement function `get_velocity`. It should return a `Vector2D` that is equal to its velocity times direction.
* In class `Ball` implement function `add_to_velocity(self, v)`. It should take a `Vector2D` as input and add it to the internal variable that stores ball's velocity.
* Modify `collide_ball_block` function. Now it should return `True` if collision occured and `False` otherwise.
* Modify `timer_tick` function so that if collision occures velocity of the racket is added to the velocity of the ball.


**Part E**
* Modify `timer_tick` function so that if collision with upper fied border of lower field border occurs the game is stopped -- first call `publish_message` with some meaningfull message (e.g. "Game stopped, press Enter to restart"), than stop the game calling `wait_for_key_and_start`.
* Run and test your code
* Create global variables to store scores of the two players. Modify these variables on collisions with borders. Print every timer tick the scores with `publish_message` function.
* Change the end-game message so that it states who won the current round and the total score.



In [0]:
%%embed_into_game ball

import math
import random

total_w = 1000
total_h = 600


class Vector2D:
  # copy your code from previous example here

def clamp(x, x_min, x_max):
  # copy your code from previous example here

class Ball:
  def __init__(self, r, color, p, v, g):
    # copy your code from previous example here

  def get_coordinates(self): 
    # copy your code from previous example here

  def get_properties(self): 
    # copy your code from previous example here

  def move_and_view(self):
    # copy your code from previous example here

  def collide(self, v, u):
    # copy your code from previous example here

  def add_to_velocity(self, v):
    pass # Remove 'pass' and enter your code here

class Block:
  def __init__(self, p, size, color="blue", v=0.0, direction=Vector2D(0, 0)):
    # copy your code from previous example here

  def set_direction(self, direction):
    # copy your code from previous example here

  def move_and_view(self):
    # copy your code from previous example here

  def get_sizes(self):
    # copy your code from previous example here
  
  def get_properties(self): 
    # copy your code from previous example here

  def get_velocity(self): 
    pass # Remove 'pass' and enter your code here


def publish_message(msg):
  print(msg)

def collide_ball_block(ball, block):
  # copy your code from previous example here

player_up_score, player_down_score = 0, 0

# This function will be called on timer
# It should perform one step of evolution 
# Update positon ob the ball here
def timer_tick(key_left, key_right):
  pass # Remove 'pass' and enter your code here

def wait_for_key_and_start():
  pass # Remove 'pass' and enter your code here

wait_for_key_and_start()

###Solution

In [0]:
%%embed_into_game ball

import math
import random

total_w = 1000
total_h = 600


class Vector2D:
  def __init__(self, x=0, y=0): self.x, self.y = x, y
  def __add__(self, other): return Vector2D(self.x + other.x, self.y + other.y)
  def __sub__(self, other): return Vector2D(self.x - other.x, self.y - other.y)
  def __mul__(self, num): return Vector2D(self.x * num, self.y * num)
  def __rmul__(self, other): return self.__mul__(other)

def clamp(x, x_min, x_max):
  if x < x_min: return x_min
  if x > x_max: return x_max
  return x

class Ball:
  def __init__(self, r, color, p, v, g):
    self.r, self.color = r, color
    self.p, self.v, self.g = p, v, g

  # do not change the signature of this methods
  # it is needed for correct drawing
  def get_coordinates(self): return self.p
  def get_properties(self): return self.r, self.color

  def move_and_view(self):
    self.p += self.v
    self.v.y -= self.g
    self.v = Vector2D(clamp(self.v.x, -self.r/2, self.r/2), clamp(self.v.y, -self.r/2, self.r/2)) 

  def collide(self, v, u):
    d = u - v
    r = self.p - v
    if ((0 < r.y**2 < d.y*r.y) and (abs(r.x) < self.r)):
      self.v.x *= (2*(r.x * self.v.x >= 0) - 1)
      return True
    if ((0 < r.x**2 < d.x*r.x) and (abs(r.y) < self.r)):
      self.v.y *= (2*(r.y * self.v.y >= 0) - 1)
      return True
    return False

  def add_to_velocity(self, v):
    self.v += v

class Block:
  def __init__(self, p, size, color="blue", v=0.0, direction=Vector2D(0, 0)):
    self.p, self.size, self.color, self.v = p, size, color, v
    self.direction = direction

  def set_direction(self, direction):
    self.direction = direction

  def move_and_view(self):
    self.p += self.v * self.direction
    self.p = Vector2D(clamp(self.p.x, 0, total_w - self.size.x), clamp(self.p.y, 0, total_h - self.size.y))
    return self.p.y > 0

  def get_sizes(self): return self.p, self.size
  def get_velocity(self): return self.v * self.direction
  def get_properties(self): return self.color


def publish_message(msg):
  print(msg)

def collide_ball_block(ball, block):
  p, size = block.get_sizes()
  sides = [[Vector2D(p.x, p.y), Vector2D(p.x + size.x, p.y)],
            [Vector2D(p.x + size.x, p.y), Vector2D(p.x + size.x, p.y + size.y)],
            [Vector2D(p.x + size.x, p.y + size.y), Vector2D(p.x, p.y + size.y)],
            [Vector2D(p.x, p.y + size.y), Vector2D(p.x, p.y + size.y)]]
  for p1, p2 in sides:
    if ball.collide(p1, p2):
      ball.add_to_velocity(block.get_velocity())
      return True
  return False

player_up_score, player_down_score = 0, 0

# This function will be called on timer
# It should perform one step of evolution 
# Update positon ob the ball here
def timer_tick(key_left, key_right):
  global player_up_score, player_down_score
  ball.collide(Vector2D(0, 0), Vector2D(0, total_h))
  ball.collide(Vector2D(total_w, 0), Vector2D(total_w, total_h))
  if ball.collide(Vector2D(total_w, 0), Vector2D(0, 0)):
    player_up_score += 1
    publish_message("UP WON; PRESS ENTER TO RESTART")
    wait_for_key_and_start()
  if ball.collide(Vector2D(total_w, total_h), Vector2D(0, total_h)):
    player_down_score += 1
    publish_message("DOWN WON; PRESS ENTER TO RESTART")
    wait_for_key_and_start()
  collide_ball_block(ball, r1)
  collide_ball_block(ball, r2)
  ball.move_and_view()
  r1.set_direction(Vector2D(key_left, 0))
  r1.move_and_view()
  r2.set_direction(Vector2D(key_right, 0))
  r2.move_and_view()
  publish_message("scores UP: " + str(player_up_score) + " ; DOWN: " + str(player_down_score))

def wait_for_key_and_start():
  global ball, r1, r2
  direction = 2 * (random.randint(0, 1) - 0.5)
  angle = (random.random() - 0.5) * 3.0
  ball = Ball(10, 'red', Vector2D(total_w/2, total_h/2), Vector2D(2.0 * math.sin(angle), 2.0 * math.cos(angle) * direction), 0.0)
  r1 = Block(Vector2D(total_w/2 - 100, 5), Vector2D(200, 15), "green", v=5.0)
  r2 = Block(Vector2D(total_w/2 - 100, total_h - 20), Vector2D(200, 15), "blue", v=5.0)

wait_for_key_and_start()

##Problem

In [0]:
%%embed_into_game ball

import math
import random

total_w = 1000
total_h = 600


class Vector2D:
  def __init__(self, x=0, y=0): self.x, self.y = x, y
  def __add__(self, other): return Vector2D(self.x + other.x, self.y + other.y)
  def __sub__(self, other): return Vector2D(self.x - other.x, self.y - other.y)
  def __mul__(self, num): return Vector2D(self.x * num, self.y * num)
  def __rmul__(self, other): return self.__mul__(other)

def clamp(x, x_min, x_max):
  if x < x_min: return x_min
  if x > x_max: return x_max
  return x

class Ball:
  def __init__(self, r, color, p, v, g):
    self.r, self.color = r, color
    self.p, self.v, self.g = p, v, g

  # do not change the signature of this methods
  # it is needed for correct drawing
  def get_coordinates(self): return self.p
  def get_properties(self): return self.r, self.color

  def move_and_view(self):
    self.p += self.v
    self.v.y -= self.g
    self.v = Vector2D(clamp(self.v.x, -self.r/2, self.r/2), clamp(self.v.y, -self.r/2, self.r/2)) 

  def collide(self, v, u):
    d = u - v
    r = self.p - v
    if ((0 < r.y**2 < d.y*r.y) and (abs(r.x) < self.r)):
      self.v.x *= (2*(r.x * self.v.x >= 0) - 1)
      return True
    if ((0 < r.x**2 < d.x*r.x) and (abs(r.y) < self.r)):
      self.v.y *= (2*(r.y * self.v.y >= 0) - 1)
      return True
    return False

  def add_to_velocity(self, v):
    self.v += v

class Block:
  def __init__(self, p, size, color="blue", v=0.0, direction=Vector2D(0, 0)):
    self.p, self.size, self.color, self.v = p, size, color, v
    self.direction = direction

  def set_direction(self, direction):
    self.direction = direction

  def move_and_view(self):
    self.p += self.v * self.direction
    self.p = Vector2D(clamp(self.p.x, 0, total_w - self.size.x), clamp(self.p.y, 0, total_h - self.size.y))
    return self.p.y > self.size.y + 10

  def get_sides(self):
    return [[Vector2D(self.p.x, self.p.y), Vector2D(self.p.x + self.size.x, self.p.y)],
            [Vector2D(self.p.x + self.size.x, self.p.y), Vector2D(self.p.x + self.size.x, self.p.y + self.size.y)],
            [Vector2D(self.p.x + self.size.x, self.p.y + self.size.y), Vector2D(self.p.x, self.p.y + self.size.y)],
            [Vector2D(self.p.x, self.p.y + self.size.y), Vector2D(self.p.x, self.p.y + self.size.y)]]
  
  def get_sizes(self): return self.p, self.size
  def get_velocity(self): return self.v * self.direction
  def get_properties(self): return self.color


def collide_ball_segments(ball, segments):
  for p1, p2 in segments:
    if ball.collide(p1, p2): return True
  return False

def collide_ball_block(ball, block):
  if collide_ball_segments(ball, block.get_sides()):
    ball.add_to_velocity(block.get_velocity())
    return True
  return False

score = 0
counter_to_new_blk = 0
blocks = []

# This function will be called on timer
# It should perform one step of evolution 
# Update positon ob the ball here
def timer_tick(key_left, key_right):
  global score, counter_to_new_blk, blocks
  collide_ball_segments(ball, [[Vector2D(0, 0), Vector2D(0, total_h)]])
  collide_ball_segments(ball, [[Vector2D(total_w, 0), Vector2D(total_w, total_h)]])
  collide_ball_segments(ball, [[Vector2D(total_w, total_h), Vector2D(0, total_h)]])
  if collide_ball_segments(ball, [[Vector2D(total_w, 0), Vector2D(0, 0)]]):
    publish_message("GAME OVER. Score: " + str(score) + "; PRESS ENTER TO RESTART")
    wait_for_key_and_start()

  new_blocks = [blk for blk in blocks if not collide_ball_block(ball, blk)]
  score += len(blocks) - len(new_blocks)
  blocks = new_blocks

  counter_to_new_blk += 1
  if counter_to_new_blk > 1000:
    blocks = blocks + [Block(Vector2D(10 + x * 160, total_h - 60), Vector2D(150, 50), v=0.1, direction=Vector2D(0, -1)) for x in range(total_w // 160)]
    counter_to_new_blk = 0

  for block in blocks:
    if block.move_and_view():
      publish_message("GAME OVER. Score: " + str(score) + "; PRESS ENTER TO RESTART")
      wait_for_key_and_start()

  collide_ball_block(ball, r)
  ball.move_and_view()
  r.set_direction(Vector2D(key_left, 0))
  r.move_and_view()
  publish_message("score: " + str(score))

def wait_for_key_and_start():
  global counter_to_new_blk, score, ball, r, blocks
  score = 0
  counter_to_new_blk = 0
  blocks = [Block(Vector2D(10 + x * 160, total_h - 60), Vector2D(150, 50), v=0.1, direction=Vector2D(0, -1)) for x in range(total_w // 160)]
  ball = Ball(10, 'red', Vector2D(total_w/2, 40), Vector2D(0, 10.0), 0.0)
  r = Block(Vector2D(total_w/2 - 100, 5), Vector2D(200, 15), "green", v=10.0)

def publish_message(msg):
  print(msg)

wait_for_key_and_start()

* **Problem 1:** Implement the "Snake game" by filling in the missing parts of code (see comments in the following code section).
* **Problem 2:** Make sure that all unit-tests are passing. Fix any bugs you find. You can use `%%debug_cell_with_pytutor` to make debug easier, but do not forget to remove it after you finish debugging.
* **Problem 3:** Add `%%embed_into_game snake` at the top of the cell and try playing the game. Use "wasd" for control.

In [3]:
%%embed_into_game snake
# This is the complete code
# I will remove parts of it and replace with appropriate comments.

import random

class Apple:
  def __init__(self, w, h):
    self.pos = [0, 0]
    self.w = w
    self.h = h
        
  def reset(self):
    self.pos = [random.randint(0, self.w - 1), random.randint(0, self.h - 1)]

  def get_apple(self):
    return self.pos

class Snake:
  def __init__(self, w, h):
    self.w, self.h = w, h
    self.reset()
        
  def move_one_step(self):
    head = [self.pos[0][0] + self.direction[0], self.pos[0][1] + self.direction[1]]
    if not self.grow:
      self.pos = [head] + self.pos[:-1]
    else:
      self.pos = [head] + self.pos
      self.grow = False
    
  def set_direction(self, direction):
    if not self.direction[0] * direction[0] + self.direction[1] * direction[1]:
      self.direction = direction
    
  def get_snake(self):
    return self.pos
    
  def reset(self):
    self.pos = [[self.w/2, self.h/2], [self.w/2, self.h/2 + 1]]
    self.direction = [0, -1]
    self.grow = False
        
  def grow_on_next_step(self):
    self.grow = True
        
  def head_collision(self):
    head = self.pos[0]
    if head[0] < 0 or head[0] >= self.w:
      return True
    if head[1] < 0 or head[1] >= self.h:
      return True
    if head in self.pos[1:]:
      return True
    return False

snake = Snake(15, 15)
assert isinstance(snake, Snake), "Not instance of snake"
# I will put much more tests here
print("ALL TESTS SUCCESSFULLY PASSED")